In [31]:
from hcloud import Client
client = Client(
    token="KccUEiddxtzGoLWSNC3V8tylq7MYHCjdnShtgasQ8jSbHqCjGoaa6Rq7yoz4uS23"
)
PREFIX = "s444498"
YOUR_LOCAL_SSH_PUBKEY = "ssh-ed25519 AAAAC3NzaC1lZDI1NTE5AAAAIAj15oTbXA0KGBw5V/76KXDgJZpLNrxUO/rTA0u0eRl1 wirus@wirusowylapek"
try:
    ssh_key = client.ssh_keys.create(name=f"{PREFIX}-pzc-ssh-key-2", public_key=YOUR_LOCAL_SSH_PUBKEY)
    print(f"Key {ssh_key.data_model.name} created: {ssh_key.data_model.public_key}")
except:
    ssh_key = client.ssh_keys.get_by_name(f"{PREFIX}-pzc-ssh-key-2")
    print(f"Key {ssh_key.data_model.name} already in use: {ssh_key.data_model.public_key}")

Key s444498-pzc-ssh-key-2 already in use: ssh-ed25519 AAAAC3NzaC1lZDI1NTE5AAAAIAj15oTbXA0KGBw5V/76KXDgJZpLNrxUO/rTA0u0eRl1 wirus@wirusowylapek


In [32]:
from hcloud.networks.domain import NetworkSubnet

try:
    vnet = client.networks.create(
        name=f"{PREFIX}-pzc-test-vnet", 
        ip_range="10.10.10.0/24", 
        subnets=[
            NetworkSubnet(ip_range="10.10.10.0/24", network_zone="eu-central", type="cloud")
        ]
    )
    print(f"Created network: {vnet.data_model.name} ({vnet.data_model.ip_range})")
except:
    vnet = client.networks.get_by_name(
        f"{PREFIX}-pzc-test-vnet", 
    )
    print(f"Network in use: {vnet.data_model.name} ({vnet.data_model.ip_range})")

Network in use: s444498-pzc-test-vnet (10.10.10.0/24)


In [33]:
from hcloud.locations.domain import Location
from hcloud.images.domain import Image
from hcloud.server_types.domain import ServerType

cloud_init_gitea=r'''#cloud-config
packages:
  - apt-transport-https
  - ca-certificates
  - curl
  - gnupg-agent
  - software-properties-common

write_files:
  - path: /root/docker-compose.yml
    content: |
        version: "3"

        networks:
          gitea:
            external: false

        services:
          server:
            image: gitea/gitea:1.17.4
            container_name: gitea
            environment:
              - USER_UID=1000
              - USER_GID=1000
              - GITEA__server__DOMAIN=${DOMAIN}
              - GITEA__database__DB_TYPE=mysql
              - GITEA__database__HOST=10.10.10.2:3306
              - GITEA__database__NAME=gitea
              - GITEA__database__USER=gitea
              - GITEA__database__PASSWD=gitea
            restart: always
            networks:
              - gitea
            volumes:
              - ./data:/root/gitea
              - ./config:/root/gitea/config
              - /etc/timezone:/etc/timezone:ro
              - /etc/localtime:/etc/localtime:ro
              - /mnt/volume:/data
            ports:
              - "3000:3000"
              - "222:22"
'''
runcmd = f'''
runcmd:
  - curl -fsSL https://download.docker.com/linux/ubuntu/gpg | apt-key add -
  - add-apt-repository "deb [arch=amd64] https://download.docker.com/linux/ubuntu $(lsb_release -cs) stable"
  - apt-get update -y
  - apt-get install -y docker-ce docker-ce-cli containerd.io
  - curl -L "https://github.com/docker/compose/releases/download/1.29.2/docker-compose-$(uname -s)-$(uname -m)" -o /usr/local/bin/docker-compose
  - chmod +x /usr/local/bin/docker-compose
  - systemctl start docker
  - systemctl enable docker
  - cd /root/
  - IP=$(hostname -I | cut -d ' ' -f 1)
  - echo "DOMAIN=$IP" >> .env
  - docker-compose up -d
'''

cloud_init_gitea += runcmd

gitea_server = client.servers.create(
    name=f"{PREFIX}-gitea", 
    server_type=ServerType("cx11"), 
    image=Image(name="ubuntu-20.04"), 
    ssh_keys=[ssh_key], 
    networks=[vnet], 
    location=Location("hel1"), 
    user_data=cloud_init_gitea
)

gitea_server.action.wait_until_finished()
print(f"Creating gitea server: {gitea_server.action.complete}")

Creating gitea server: True
